In [1]:
from dataclasses import dataclass


@dataclass
class Tape:
    
    tape: dict[int, str]
    blank : str = " "
    current : int = None
    
    def __getitem__(self,index):
        return self.tape[index] if index in self.tape else self.blank
    def __setitem__(self, index, s):
        self.tape[index] = s
    def idx_range(self):
        return min(self.tape.keys()), max(self.tape.keys())+1
    
    def __str__(self):
        t = ""
        
        for i in range(*self.idx_range()):
            t += self.tape[i]
        if self.current is not None:
            try:
                t = f"{t[:self.current]}[{t[self.current]}]{t[self.current+1:]}"
            except:
                t = f"{t}...[]"
        return t
            
class TuringMachine:
    def __init__(self, tape = None, blank=" ", initial_state = "s", 
                 final_states = None, transition_function = None,
                 starting_pos = None, max_steps = 300):
        if tape is None:
            tape = Tape(dict())
        elif type(tape) == str:
            tape = Tape(dict(enumerate(list(tape))))
        if final_states is None:
            final_states = set()
        if transition_function is None:
            transition_function = dict()
        self.max_steps = max_steps
        self.processed_steps = 0
        self.initial_state = initial_state 
        self.current_state = initial_state
        self.current_position = starting_pos or 0
        self.tape = tape
        self.final_states = final_states
        self.transition_function = transition_function
        self.mov_dict = {"R":1,
                         "L":-1,
                         "N":0}
        
    def __next__(self):
        current = self.tape[self.current_position]
        current_conf = (self.current_state, current)
        if current_conf in self.transition_function:
            t = self.transition_function[current_conf] # [state, char, mov]
            self.tape[self.current_position] = t[1]
            self.current_position += self.mov_dict[t[2]]
            self.current_state = t[0]
        self.processed_steps+=1
            
    def process(self, string):
        self.processed_steps = 0
        self.tape = Tape(dict(enumerate(list(string))))
        while (self.current_state not in self.final_states) and self.processed_steps<self.max_steps:
            next(self)
            self.processed_steps+=1
        tape = self.tape
        self.reset()
        return str(tape)
    
    def debug(self, string, step=1, log_func = lambda *x : print(*x)):
        self.processed_steps = 0
        self.tape = Tape(dict(enumerate(list(string))))
        flag = True
        
        while flag:
            self.tape.current = self.current_position
            log_func(self.current_state, self.tape)
            for i in range(step):
                if (self.current_state in self.final_states) or self.processed_steps>self.max_steps:
                    flag = False
                    break
                self.processed_steps+=1
                next(self)
            
        tape = self.tape
        self.reset()
        return str(tape)
    
    def reset(self):
        self.processed_steps = 0
        self.current = None
        self.current_position = 0
        self.tape = None
        self.current_state = self.initial_state

def to_unary(n):
    return "1"*n
def from_unary(n):
    return n.count("1")
def from_unary_div(n, div):
    q,r = n.replace("[","").replace("]","").split("=")
    return {"div":from_unary(q)/div+from_unary(r),
            "int_div":from_unary(r),
            "module":from_unary(q)}

In [2]:
initial_state = "s"
transition_function = {("s","0"):("s", "1", "R"),
                       ("s","1"):("s", "0", "R"),
                       ("s"," "):("f"," ", "N"),
                       }
final_states = {"f"}

t = TuringMachine(
                  initial_state = "s",
                  final_states = final_states,
                  transition_function=transition_function)

In [3]:
t.process("010011001 ")

'101100110 '

In [4]:
t.debug("010011001 ")

s [0]10011001 
s 1[1]0011001 
s 10[0]011001 
s 101[0]11001 
s 1011[1]1001 
s 10110[1]001 
s 101100[0]01 
s 1011001[0]1 
s 10110011[1] 
s 101100110[ ]
f 101100110[ ]


'101100110[ ]'

In [5]:

transition_function = {("0","0"):("0", "0", "R"),
                       ("0","1"):("0", "1", "R"),
                       ("0"," "):("1"," ", "R"),
                       
                       ("1","0"):("1", "0", "R"),
                       ("1","1"):("1", "1", "R"),
                       ("1"," "):("2"," ", "L"),
                       
                       ("2","0"):("2", "1", "L"),
                       ("2","1"):("3", "0", "L"),
                       ("2"," "):("5"," ", "R"),
                       
                       ("3","0"):("3", "0", "L"),
                       ("3","1"):("3", "1", "L"),
                       ("3"," "):("4"," ", "L"),
                       
                       ("4","0"):("0", "1", "R"),
                       ("4","1"):("4", "0", "L"),
                       ("4"," "):("0","1", "R"),
                       
                       ("5","1"):("5", " ", "R"),
                       ("5"," "):("f", " ", "N"),

                       }
final_states = {"f"}

t = TuringMachine(
                  initial_state = "0",
                  final_states = final_states,
                  transition_function=transition_function, 
                  max_steps = 100000)

In [6]:
t.debug("11 11111")

0 [1]1 11111
0 1[1] 11111
0 11[ ]11111
1 11 [1]1111
1 11 1[1]111
1 11 11[1]11
1 11 111[1]1
1 11 1111[1]
1 11 11111...[]
2 11 1111[1] 
3 11 111[1]0 
3 11 11[1]10 
3 11 1[1]110 
3 11 [1]1110 
3 11[ ]11110 
4 1[1] 11110 
4 [1]0 11110 
4 00 11110[ ]00 11110 
0 [1]00 11110 
0 1[0]0 11110 
0 10[0] 11110 
1 100[ ]11110 
1 100 [1]1110 
1 100 1[1]110 
1 100 11[1]10 
1 100 111[1]0 
1 100 1111[0] 
2 100 111[1]0 
2 100 11[1]11 
3 100 1[1]101 
3 100 [1]1101 
3 100[ ]11101 
3 10[0] 11101 
4 1[0]0 11101 
0 10[1] 11101 
1 101[ ]11101 
1 101 [1]1101 
1 101 1[1]101 
1 101 11[1]01 
1 101 111[0]1 
1 101 1110[1] 
2 101 111[0]1 
3 101 11[1]00 
3 101 1[1]100 
3 101 [1]1100 
3 101[ ]11100 
3 10[1] 11100 
4 1[0]1 11100 
4 [1]00 11100 
0 1[1]0 11100 
0 11[0] 11100 
1 110[ ]11100 
1 110 [1]1100 
1 110 1[1]100 
1 110 11[1]00 
1 110 111[0]0 
1 110 1110[0] 
2 110 111[0]0 
2 110 11[1]01 
2 110 1[1]111 
3 110 [1]1011 
3 110[ ]11011 
3 11[0] 11011 
4 1[1]0 11011 
0 11[1] 11011 
1 111[ ]11011 
1 111 [1]1011 
1 111 1[1]

'100010  [ ]    '

In [7]:
transition_function = {
                       ("0","1"):("0", "1", "R"),
                       ("0"," "):("1"," ", "R"),
                       
                       ("1","1"):("1", "1", "R"),
                       ("1"," "):("2"," ", "L"),
                       
                       ("2","1"):("3", " ", "L"),
                       ("2"," "):("f"," ", "N"),
    
                        ("3","1"):("3","1", "L"),
                        ("3"," "):("4"," ", "L"),
    
    
                     ("4","1"):("4","1", "L"),
                        ("4"," "):("5"," ", "R"),
    
                     ("5","1"):("0"," ", "R"),
                        ("5"," "):("f"," ", "N"),


                       }
final_states = {"f"}

t = TuringMachine(
                  initial_state = "0",
                  final_states = final_states,
                  transition_function=transition_function, 
                  max_steps = 100000)

In [8]:

from_unary(t.debug(f"{to_unary(7)} {to_unary(3)}"))

0 [1]111111 111
0 1[1]11111 111
0 11[1]1111 111
0 111[1]111 111
0 1111[1]11 111
0 11111[1]1 111
0 111111[1] 111
0 1111111[ ]111
1 1111111 [1]11
1 1111111 1[1]1
1 1111111 11[1]
1 1111111 111...[]
2 1111111 11[1] 
3 1111111 1[1]  
3 1111111 [1]1  
3 1111111[ ]11  
4 111111[1] 11  
4 11111[1]1 11  
4 1111[1]11 11  
4 111[1]111 11  
4 11[1]1111 11  
4 1[1]11111 11  
4 [1]111111 11  
4 1111111 11 [ ]1111111 11  
5 [ ]1111111 11  
0  [ ]111111 11  
0   [1]11111 11  
0   1[1]1111 11  
0   11[1]111 11  
0   111[1]11 11  
0   1111[1]1 11  
0   11111[1] 11  
1   111111[ ]11  
1   111111 [1]1  
1   111111 1[1]  
2   111111 [1]1  
3   111111[ ]1   
3   11111[1] 1   
4   1111[1]1 1   
4   111[1]11 1   
4   11[1]111 1   
4   1[1]1111 1   
4   [1]11111 1   
4  [ ]111111 1   
4 [ ] 111111 1   
5  [ ]111111 1   
0   [ ]11111 1   
0    [1]1111 1   
0    1[1]111 1   
0    11[1]11 1   
0    111[1]1 1   
0    1111[1] 1   
1    11111[ ]1   
1    11111 [1]   
2    11111[ ]1   
3    1111[1]     
4    111[1]1 

4

In [9]:
transition_function = {
                       ("0","1"):("1", " ", "R"),
                       ("0"," "):("12"," ", "L"),
                       
                       ("1","1"):("1", "1", "R"),
                       ("1"," "):("2"," ", "R"),
                       
                       ("2","1"):("4", "Y", "R"),
                       ("2","="):("3","=", "L"),
    
                        ("3","Y"):("3","1", "L"),
                        ("3"," "):("9"," ", "L"),
    
    
                     ("4","1"):("4","1", "R"),
                        ("4","="):("5","=", "R"),
    
                     ("5","1"):("5","1", "R"),
                        ("5"," "):("6","1", "L"),
                    
                    ("6","1"):("6","1", "L"),
                        ("6","="):("7","=", "L"),
                        
                        ("7","1"):("7","1", "L"),
                        ("7","Y"):("8","Y", "R"),
    
                       ("8","="):("3","=", "L"),
                       ("8","1"):("4","Y", "R"),
    
                    ("9","1"):("9","1", "L"),
                        ("9"," "):("0"," ", "R"),
    
 
                    ("11"," "):("13"," ", "R"),
                    ("11","Y"):("13"," ", "R"),
                    ("11","1"):("13"," ", "R"),
                        
    
                    ("12"," "):("12","1", "L"),
                        ("12"," "):("11"," ", "R"),
    
                    ("13"," "):("13"," ", "R"),
                    ("13","1"):("13"," ", "R"),
                    ("13","="):("f"," ", "R"),
                       


                       }
final_states = {"f"}

t = TuringMachine(
                  initial_state = "0",
                  final_states = final_states,
                  transition_function=transition_function, 
                  max_steps = 1000000)

In [10]:

from_unary(t.debug(f"{to_unary(8)} {to_unary(5)}="))

0 [1]1111111 11111=
1  [1]111111 11111=
1  1[1]11111 11111=
1  11[1]1111 11111=
1  111[1]111 11111=
1  1111[1]11 11111=
1  11111[1]1 11111=
1  111111[1] 11111=
1  1111111[ ]11111=
2  1111111 [1]1111=
4  1111111 Y[1]111=
4  1111111 Y1[1]11=
4  1111111 Y11[1]1=
4  1111111 Y111[1]=
4  1111111 Y1111[=]
5  1111111 Y1111=...[]
6  1111111 Y1111[=]1
7  1111111 Y111[1]=1
7  1111111 Y11[1]1=1
7  1111111 Y1[1]11=1
7  1111111 Y[1]111=1
7  1111111 [Y]1111=1
8  1111111 Y[1]111=1
4  1111111 YY[1]11=1
4  1111111 YY1[1]1=1
4  1111111 YY11[1]=1
4  1111111 YY111[=]1
5  1111111 YY111=[1]
5  1111111 YY111=1...[]
6  1111111 YY111=[1]1
6  1111111 YY111[=]11
7  1111111 YY11[1]=11
7  1111111 YY1[1]1=11
7  1111111 YY[1]11=11
7  1111111 Y[Y]111=11
8  1111111 YY[1]11=11
4  1111111 YYY[1]1=11
4  1111111 YYY1[1]=11
4  1111111 YYY11[=]11
5  1111111 YYY11=[1]1
5  1111111 YYY11=1[1]
5  1111111 YYY11=11...[]
6  1111111 YYY11=1[1]1
6  1111111 YYY11=[1]11
6  1111111 YYY11[=]111
7  1111111 YYY1[1]=111
7  1111111 YYY[1]1=1

40

In [11]:
transition_function = {
                       ("0","1"):("0", "1", "R"),
                       ("0"," "):("0"," ", "R"),
                        ("0","="):("6","=", "R"),
    
                        ("6","1"):("6","1", "R"),
                        ("6"," "):("7","1", "L"), #Acumule
    
                        ("7","1"):("7","1", "L"),
                        ("7","="):("1","=", "L"),
                       
                       ("1","1"):("1", "Y", "L"),
                       ("1"," "):("2"," ", "R"),
                       
                       ("2","Y"):("3", "1", "L"),
                        ("2"," "):("2", " ", "R"),
                        ("2","1"):("2", "1", "R"),
                       ("2","="):("6","=", "R"),
    
                        ("3","1"):("3","1", "L"),
                        ("3"," "):("4"," ", "L"),
    
                        ("4","1"):("4","1", "L"),
                        ("4"," "):("5"," ", "R"),
                
                        ("5","1"):("2"," ", "R"),
                        ("5"," "):("b"," ", "R"),
    
                        ("b","1"):("b"," ", "R"),
                        ("b"," "):("b"," ", "R"),
                        ("b","Y"):("b"," ", "R"),
                        ("b","="):("b1"," ", "R"),
    
                        ("b1","1"):("f"," ", "R"),
                        ("b1"," "):("f"," ", "R"),
    
                    
    


                       }
final_states = {"f"}

t = TuringMachine(
                  initial_state = "0",
                  final_states = final_states,
                  transition_function=transition_function, 
                  max_steps = 100000)

In [12]:
from_unary(t.debug(f"{to_unary(13)} {to_unary(5)}="))

0 [1]111111111111 11111=
0 1[1]11111111111 11111=
0 11[1]1111111111 11111=
0 111[1]111111111 11111=
0 1111[1]11111111 11111=
0 11111[1]1111111 11111=
0 111111[1]111111 11111=
0 1111111[1]11111 11111=
0 11111111[1]1111 11111=
0 111111111[1]111 11111=
0 1111111111[1]11 11111=
0 11111111111[1]1 11111=
0 111111111111[1] 11111=
0 1111111111111[ ]11111=
0 1111111111111 [1]1111=
0 1111111111111 1[1]111=
0 1111111111111 11[1]11=
0 1111111111111 111[1]1=
0 1111111111111 1111[1]=
0 1111111111111 11111[=]
6 1111111111111 11111=...[]
7 1111111111111 11111[=]1
1 1111111111111 1111[1]=1
1 1111111111111 111[1]Y=1
1 1111111111111 11[1]YY=1
1 1111111111111 1[1]YYY=1
1 1111111111111 [1]YYYY=1
1 1111111111111[ ]YYYYY=1
2 1111111111111 [Y]YYYY=1
3 1111111111111[ ]1YYYY=1
4 111111111111[1] 1YYYY=1
4 11111111111[1]1 1YYYY=1
4 1111111111[1]11 1YYYY=1
4 111111111[1]111 1YYYY=1
4 11111111[1]1111 1YYYY=1
4 1111111[1]11111 1YYYY=1
4 111111[1]111111 1YYYY=1
4 11111[1]1111111 1YYYY=1
4 1111[1]11111111 1YYYY=1
4 11

2

In [13]:
# starts accumulating after the =
# changes every 1 from the divisor to y's
# starts changing the y's to 1's, for each such operation deletes a 1 from the dividend
# goes back to delete all the y's
# after all y's are deleted puts 1 to the accumulator and repeats


transition_function = {
                       ("0","1"):("0", "1", "R"),
                       ("0"," "):("0"," ", "R"),
                        ("0","="):("6","=", "R"),
    
                        ("6","1"):("6","1", "R"),
                        ("6"," "):("7","1", "L"), #Acumule
    
                        ("7","1"):("7","1", "L"),
                        ("7","="):("1","=", "L"),
                       
                       ("1","1"):("1", "Y", "L"),
                       ("1"," "):("2"," ", "R"),
                       
                       ("2","Y"):("3", "1", "L"),
                        ("2"," "):("2", " ", "R"),
                        ("2","1"):("2", "1", "R"),
                       ("2","="):("6","=", "R"),
    
                        ("3","1"):("3","1", "L"),
                        ("3"," "):("4"," ", "L"),
    
                        ("4","1"):("4","1", "L"),
                        ("4"," "):("5"," ", "R"),
                
                        ("5","1"):("2"," ", "R"),
                        ("5"," "):("b"," ", "R"),
    
                        ("b","1"):("b1"," ", "R"),
                        ("b"," "):("f"," ", "R"),
    
                        ("b1","1"):("b1","1", "R"),
                         ("b1","Y"):("b1"," ", "R"),
                        ("b1"," "):("b1"," ", "R"),
                        ("b1","="):("b2","=", "R"),
                        ("b2","1"):("f"," ", "N"),
    
                        

                    
    


                       }
final_states = {"f"}

t = TuringMachine(
                  initial_state = "0",
                  final_states = final_states,
                  transition_function=transition_function, 
                  max_steps = 100000)

In [22]:
d = 21
n = 6
from_unary_div(t.debug(f"{to_unary(d)} {to_unary(n)}="), n)

0 [1]11111111111111111111 111111=
0 1[1]1111111111111111111 111111=
0 11[1]111111111111111111 111111=
0 111[1]11111111111111111 111111=
0 1111[1]1111111111111111 111111=
0 11111[1]111111111111111 111111=
0 111111[1]11111111111111 111111=
0 1111111[1]1111111111111 111111=
0 11111111[1]111111111111 111111=
0 111111111[1]11111111111 111111=
0 1111111111[1]1111111111 111111=
0 11111111111[1]111111111 111111=
0 111111111111[1]11111111 111111=
0 1111111111111[1]1111111 111111=
0 11111111111111[1]111111 111111=
0 111111111111111[1]11111 111111=
0 1111111111111111[1]1111 111111=
0 11111111111111111[1]111 111111=
0 111111111111111111[1]11 111111=
0 1111111111111111111[1]1 111111=
0 11111111111111111111[1] 111111=
0 111111111111111111111[ ]111111=
0 111111111111111111111 [1]11111=
0 111111111111111111111 1[1]1111=
0 111111111111111111111 11[1]111=
0 111111111111111111111 111[1]11=
0 111111111111111111111 1111[1]1=
0 111111111111111111111 11111[1]=
0 111111111111111111111 111111[=]
6 111111111111

{'div': 3.5, 'int_div': 3, 'module': 3}

In [23]:
d = 5
n = 10
from_unary_div(t.debug(f"{to_unary(d)} {to_unary(n)}="), n)

0 [1]1111 1111111111=
0 1[1]111 1111111111=
0 11[1]11 1111111111=
0 111[1]1 1111111111=
0 1111[1] 1111111111=
0 11111[ ]1111111111=
0 11111 [1]111111111=
0 11111 1[1]11111111=
0 11111 11[1]1111111=
0 11111 111[1]111111=
0 11111 1111[1]11111=
0 11111 11111[1]1111=
0 11111 111111[1]111=
0 11111 1111111[1]11=
0 11111 11111111[1]1=
0 11111 111111111[1]=
0 11111 1111111111[=]
6 11111 1111111111=...[]
7 11111 1111111111[=]1
1 11111 111111111[1]=1
1 11111 11111111[1]Y=1
1 11111 1111111[1]YY=1
1 11111 111111[1]YYY=1
1 11111 11111[1]YYYY=1
1 11111 1111[1]YYYYY=1
1 11111 111[1]YYYYYY=1
1 11111 11[1]YYYYYYY=1
1 11111 1[1]YYYYYYYY=1
1 11111 [1]YYYYYYYYY=1
1 11111[ ]YYYYYYYYYY=1
2 11111 [Y]YYYYYYYYY=1
3 11111[ ]1YYYYYYYYY=1
4 1111[1] 1YYYYYYYYY=1
4 111[1]1 1YYYYYYYYY=1
4 11[1]11 1YYYYYYYYY=1
4 1[1]111 1YYYYYYYYY=1
4 [1]1111 1YYYYYYYYY=1
4 11111 1YYYYYYYYY=[1]11111 1YYYYYYYYY=1
5 [ ]11111 1YYYYYYYYY=1
2  [ ]1111 1YYYYYYYYY=1
2   [1]111 1YYYYYYYYY=1
2   1[1]11 1YYYYYYYYY=1
2   11[1]1 1YYYYYYYYY=1
2  

{'div': 0.5, 'int_div': 0, 'module': 5}

In [24]:

from_unary_div(t.debug(f"{to_unary(5)} {to_unary(0)}="), 10)

0 [1]1111 =
0 1[1]111 =
0 11[1]11 =
0 111[1]1 =
0 1111[1] =
0 11111[ ]=
0 11111 [=]
6 11111 =...[]
7 11111 [=]1
1 11111[ ]=1
2 11111 [=]1
6 11111 =[1]
6 11111 =1...[]
7 11111 =[1]1
7 11111 [=]11
1 11111[ ]=11
2 11111 [=]11
6 11111 =[1]1
6 11111 =1[1]
6 11111 =11...[]
7 11111 =1[1]1
7 11111 =[1]11
7 11111 [=]111
1 11111[ ]=111
2 11111 [=]111
6 11111 =[1]11
6 11111 =1[1]1
6 11111 =11[1]
6 11111 =111...[]
7 11111 =11[1]1
7 11111 =1[1]11
7 11111 =[1]111
7 11111 [=]1111
1 11111[ ]=1111
2 11111 [=]1111
6 11111 =[1]111
6 11111 =1[1]11
6 11111 =11[1]1
6 11111 =111[1]
6 11111 =1111...[]
7 11111 =111[1]1
7 11111 =11[1]11
7 11111 =1[1]111
7 11111 =[1]1111
7 11111 [=]11111
1 11111[ ]=11111
2 11111 [=]11111
6 11111 =[1]1111
6 11111 =1[1]111
6 11111 =11[1]11
6 11111 =111[1]1
6 11111 =1111[1]
6 11111 =11111...[]
7 11111 =1111[1]1
7 11111 =111[1]11
7 11111 =11[1]111
7 11111 =1[1]1111
7 11111 =[1]11111
7 11111 [=]111111
1 11111[ ]=111111
2 11111 [=]111111
6 11111 =[1]11111
6 11111 =1[1]1111
6 11111 =11

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



11111 =1111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111[1]11111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111
7 11111 =111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111[1]111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111
7 11111 =11111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111[1]1111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111
7 11111 =1111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111[1]11111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111
7 11111 =111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111[1]11111111111111111111111111111111111111111111111111111111111111111111111111

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'div': 222.5, 'int_div': 222, 'module': 5}

In [21]:

#https://stackoverflow.com/questions/59045832/turing-machine-for-addition-and-comparison-of-binary-numbers
#https://www.tutorialspoint.com/design-turing-machine-for-multiplication#